In [ ]:
import streamlit as st
import geemap.foliumap as geemap
import ee


# Initialize GEE
try:
    ee.Initialize()
except Exception as e:
    ee.Authenticate()
    ee.Initialize()

In [96]:
admin = ee.FeatureCollection("projects/ee-levice/assets/constituencies")
mvita = admin.filter(ee.Filter.eq('CONSTITUEN','MVITA'))
geometry = mvita.geometry()
print("Geometry:", geometry.getInfo())
admin.getInfo()

Geometry: {'type': 'Polygon', 'coordinates': [[[39.640164239054336, -4.039472918542136], [39.640529950765604, -4.041060357456938], [39.64095796382212, -4.048016529590386], [39.64235816166241, -4.050825735272568], [39.64412842862412, -4.0591241502841235], [39.645533043605816, -4.0606536435144065], [39.64834225610367, -4.065228635881986], [39.65115149779539, -4.068220696138537], [39.6541391344692, -4.070539421751942], [39.66195144333049, -4.078534639096465], [39.66451543307704, -4.079573576009963], [39.665737235286485, -4.077923699847631], [39.667324644292336, -4.0794487497445955], [39.672510561054736, -4.079145485817869], [39.67373236169066, -4.077620497867819], [39.674954216739216, -4.075422148672909], [39.67733535114859, -4.074017567778572], [39.679346427778405, -4.0735315187918655], [39.68075102512585, -4.0728581621900455], [39.682521288373444, -4.071453564400546], [39.681910399831594, -4.066753653260032], [39.681910399831594, -4.0652286318486786], [39.680322974261806, -4.06132247008

{'type': 'FeatureCollection',
 'columns': {'CONSTITUEN': 'String',
  'CONST_CODE': 'Float',
  'COUNTY_ASS': 'Float',
  'COUNTY_A_1': 'String',
  'COUNTY_COD': 'Float',
  'COUNTY_NAM': 'String',
  'OBJECTID': 'Long',
  'REGISTRATI': 'String',
  'REGIST_CEN': 'Float',
  'Shape_Area': 'Float',
  'Shape_Leng': 'Float',
  'system:index': 'String'},
 'version': 1732738653137082,
 'id': 'projects/ee-levice/assets/constituencies',
 'properties': {'system:asset_size': 731902},
 'features': [{'type': 'Feature',
   'geometry': {'type': 'Polygon',
    'coordinates': [[[34.754117650003224, -0.03593145517336202],
      [34.754541297156635, -0.031842426888213524],
      [34.75191937252322, -0.034161177598198623],
      [34.754117650003224, -0.03593145517336202]]]},
   'id': '00000000000000000122',
   'properties': {'CONSTITUEN': '',
    'CONST_CODE': 0,
    'COUNTY_ASS': 0,
    'COUNTY_A_1': '',
    'COUNTY_COD': 0,
    'COUNTY_NAM': '',
    'OBJECTID': 334,
    'REGISTRATI': '',
    'REGIST_CEN': 0,

In [97]:
# Define Cloud Masking Function
def cloud_mask(image):
    scored = ee.Algorithms.Landsat.simpleCloudScore(image)
    mask = scored.select(['cloud']).lte(10)
    return image.updateMask(mask)


In [98]:
# Filter Landsat 8 Data
landsat = ee.ImageCollection('LANDSAT/LC08/C02/T1_L2') \
    .filter(ee.Filter.lt('CLOUD_COVER', 20)) \
    .filter(ee.Filter.date('2014-01-01', '2024-10-01')) \
    .filter(ee.Filter.bounds(geometry)) \
    #.map(cloud_mask)
landsat

In [99]:
# Compute Median Composite
median = landsat.median().clip(geometry)
median

In [100]:
# Compute NDVI
ndvi = median.normalizedDifference(['SR_B5', 'SR_B4']).rename('NDVI')
print("NDVI:", ndvi)

NDVI: ee.Image({
  "functionInvocationValue": {
    "functionName": "Image.rename",
    "arguments": {
      "input": {
        "functionInvocationValue": {
          "functionName": "Image.normalizedDifference",
          "arguments": {
            "bandNames": {
              "constantValue": [
                "SR_B5",
                "SR_B4"
              ]
            },
            "input": {
              "functionInvocationValue": {
                "functionName": "Image.clip",
                "arguments": {
                  "geometry": {
                    "functionInvocationValue": {
                      "functionName": "Collection.geometry",
                      "arguments": {
                        "collection": {
                          "functionInvocationValue": {
                            "functionName": "Collection.filter",
                            "arguments": {
                              "collection": {
                                "functionInvocation

In [101]:
# Compute Land Surface Temperature (LST)
thermal_band = median.select('ST_B10')
lst = thermal_band.expression(
    '(Tb / (1 + (0.00115 * (Tb / 1.438)) * log(0.98))) - 273.15',
    {'Tb': thermal_band}
).rename('LST')

In [102]:
# Create Map
Map = geemap.Map(center=[-4.05, 39.67], zoom=12)
Map

In [107]:
# Add Layers to Map
Map.addLayer(ndvi, {'min': 0, 'max': 1, 'palette': [
  'FFFFFF', 'CE7E45', 'DF923D', 'F1B555', 'FCD163', '99B718',
  '74A901', '66A000', '529400', '3E8601', '207401', '056201',
  '004C00', '023B01', '012E01', '011D01', '011301']
   }, "NDVI")
Map.addLayer(lst, {'min': 25, 'max': 35, 'palette': ['blue', 'red']}, "LST")
Map

In [ ]:
%pip install leafmap

In [105]:
import leafmap